### Task 1: Static Network Analysis
* Degree (in-degree/out-degree)
* Diameter
* (Mean shortest path length)
* (Top-k eigenvalues)
* (Betweennes centrality)
* (Closeness centrality)</i>

A temporal network is goint to be analysed which consists of 678907 vertices and 4729035 edges, where each edge has time information associated with it. Some of the edges have the same source and target vertex, but are association with different timestamps. This statick network analysi, however, ignores time-information and thus we use a graph build solely on the pairs of source and target vertices.

### <font color="darkgreen">Imports, configuation and preprocessing</font>

In [1]:
import pandas as pd
import numpy as np
import networkx as nx
import matplotlib.pyplot as plt
import seaborn as sns
import math

#### Directed Graph with parallel edges (due to different timestamps of the edges between pairs of vertices)

In [2]:
wiki = open("data/tgraph_real_wikiedithyperlinks_noTime.txt", 'rb')
G_par = nx.read_edgelist(wiki, create_using=nx.MultiDiGraph())
wiki.close()

#### Directed Graph used for static network analysis

In [3]:
wiki = open("data/tgraph_real_wikiedithyperlinks_noTime.txt", 'rb')
G = nx.read_edgelist(wiki, create_using=nx.DiGraph())
wiki.close()

In [4]:
def create_dataframe(G_in):
    df_edge_in = pd.DataFrame(list(G_in.in_degree()), columns=['node', 'in edges'])
    df_edge_out = pd.DataFrame(list(G_in.out_degree()), columns=['node', 'out edges'])
    df_total = pd.merge(df_edge_in, df_edge_out, on='node')
    df_total.index = df_total.index + 1
    return df_total

In [5]:
wiki_df_par = create_dataframe(G_par)

In [6]:
wiki_df = create_dataframe(G)
wiki_df.head()

node  in edges  out edges
1    1        28         88
2    6        10          0
3    8        62          6
4    9      1375        477
5    3      1068        451

### <font color="darkgreen">1. Static Network Analysis:</font> Degree distribution

The first network property which is going to be analyzed of the static network is the degree distribution. While it is an easily comprehensible network measure, it can still lead to interesting findings as we have seen in the previous assignment.

In [7]:
wiki_df['in edges'].mean() == wiki_df['out edges'].mean()

True

Which is expected of course since every outgoing edge is an incoming edge of the graph. This check is just done to check whether the parsing of the Graph object to a dataframe is done without any errors.

In [8]:
wiki_df['in edges'].mean()

5.3091660566174745

In [9]:
wiki_df['in edges'].max(), wiki_df['in edges'].min()

(10521, 0)

In [10]:
wiki_df['out edges'].max(), wiki_df['out edges'].min()

(4302, 0)

The mean of the incoming edges is just under above the 5 links. The node with the highest number of incoming edges has a little more than $10^4$ incoming edges, while the node with the highest number of outgoing edges has around  $4.3*10^3$ outgoing edges. These values do not implicate anything by themselves, but these values will be used in elaborations further on.

Before we continue with the static network analysis note that for the static network analysis it does not make sense to consider parallel edges. The parallel edges are edges between a pair of vertices at different time-stamps. But this gives a deceptive view in the static network analysis part. If a page has $y$ incoming edges of the same source vertex $x$, at different time-stamps it does not make sense to consider all of these parallel edges for many measures such as the degree distribution, page-rank etc. The choice is, therefore, made to continue with the network as a directed graph ($DiGraph$ in networkx) instead of a multi-directed graph ($MultiDiGraph$) for the static network analysis. These edges, however, have to be considered in part two for the Temporal Network Analysis where the time information of the edges is of the essence and techniques such as snapshot-based analysis can or even should be exploited.

Just to give you an overview of the deceiving effects it can have on the measures calculated over these two types of networks:

In [11]:
wiki_df_par['in edges'].mean(), wiki_df_par['in edges'].max(), wiki_df_par['out edges'].max()

(6.965659508592488, 15871, 15017)

It adds up the parallel edges between pair of vertices which result in a higher number of incoming and/or outgoing edges for many vertices. 

Let's continue with the analysis of the degree-distribution now that we have this pecularity out of the way. We are going to divide nodes of the network into deciles to get a better grasp of the characteristics of the top and bottom nodes when it boils down to number of incoming or outgoing edges.

In [12]:
wiki_df['decile_incoming_edges'] = pd.cut((wiki_df['in edges']), 10, labels=False)
wiki_df.loc[wiki_df.decile_incoming_edges.between(1, 9)].shape, wiki_df.loc[wiki_df.decile_incoming_edges.between(0, 1)].shape

((220, 4), (678830, 4))

In [13]:
wiki_df['decile_outgoing_edges'] = pd.cut((wiki_df['out edges']), 10, labels=False)
wiki_df.loc[wiki_df.decile_outgoing_edges.between(1, 9)].shape, wiki_df.loc[wiki_df.decile_outgoing_edges.between(0, 1)].shape

((305, 5), (678835, 5))

We see that there is a very skewed distribution among the nodes when we make splits based upon their number number of incoming or outgoing edges. There is thus a small set of nodes (i.e. pages) with relatively high number of incoming edges and a small set of nodes with a relatively high number of outgoing edges.

Let's divide the nodes in four groups such that in each quartile we have the same number of vertices (not the same as quartiles) intstead of the current configuration since this will faciliate a better comparison of the the groups considering the very skewed distribution. 

In [14]:
sorted_incoming_edges = wiki_df.sort_values(['in edges']).reset_index(drop = True)
sorted_outgoing_edges = wiki_df.sort_values(['out edges']).reset_index(drop = True)
sorted_incoming_edges.tail()

node  in edges  out edges  decile_incoming_edges  \
678902   300      7975       1686                      7   
678903  3546      8561          0                      8   
678904   146      9264          0                      8   
678905   149      9655        545                      9   
678906   394     10521       1777                      9   

        decile_outgoing_edges  
678902                      3  
678903                      0  
678904                      0  
678905                      1  
678906                      4

In [15]:
incoming_edges_q1 = sorted_incoming_edges.iloc[: math.floor(sorted_incoming_edges.shape[0] / 4)]
incoming_edges_q2 = sorted_incoming_edges.iloc[math.floor(sorted_incoming_edges.shape[0] / 4) : 2 * (math.floor(sorted_incoming_edges.shape[0] / 4))]
incoming_edges_q3 = sorted_incoming_edges.iloc[2 * (math.floor(sorted_incoming_edges.shape[0] / 4)) : 3 * (math.floor(sorted_incoming_edges.shape[0] / 4))]
incoming_edges_q4 = sorted_incoming_edges.iloc[3 * (math.floor(sorted_incoming_edges.shape[0] / 4)) :]

incoming_edges_bottom_1 = sorted_incoming_edges.iloc[: math.floor(sorted_incoming_edges.shape[0] / 100)]
incoming_edges_top_1 = sorted_incoming_edges.iloc[99 * math.floor(sorted_incoming_edges.shape[0] / 100):]

In [16]:
outgoing_edges_q1 = sorted_outgoing_edges.iloc[: math.floor(sorted_outgoing_edges.shape[0] / 4)]
outgoing_edges_q2 = sorted_outgoing_edges.iloc[math.floor(sorted_outgoing_edges.shape[0] / 4) : 2 * (math.floor(sorted_outgoing_edges.shape[0] / 4))]
outgoing_edges_q3 = sorted_outgoing_edges.iloc[2 * (math.floor(sorted_outgoing_edges.shape[0] / 4)) : 3 * (math.floor(sorted_outgoing_edges.shape[0] / 4))]
outgoing_edges_q4 = sorted_outgoing_edges.iloc[3 * (math.floor(sorted_outgoing_edges.shape[0] / 4)) :]

outgoing_edges_bottom_1 = sorted_outgoing_edges.iloc[: math.floor(sorted_outgoing_edges.shape[0] / 100)]
outgoing_edges_top_1 = sorted_outgoing_edges.iloc[99 * math.floor(sorted_outgoing_edges.shape[0] / 100):]

And just to double-check

In [17]:
(incoming_edges_q4.shape[0] + incoming_edges_q3.shape[0] + 
 incoming_edges_q2.shape[0] + incoming_edges_q1.shape[0]) == sorted_incoming_edges.shape[0]

True

Let's have a look at what there are some notable things in the devised groups

In [18]:
incoming_edges_q1['in edges'].mean(), incoming_edges_q2['in edges'].mean(), incoming_edges_q3['in edges'].mean(), incoming_edges_q4['in edges'].mean()

(0.0, 0.806753237571144, 1.8176236993742856, 18.61205215372741)

In [19]:
incoming_edges_q1['out edges'].mean(), incoming_edges_q2['out edges'].mean(), incoming_edges_q3['out edges'].mean(), incoming_edges_q4['out edges'].mean()

(3.8300142582751024, 2.36138835534921, 3.578950779491651, 11.466202004371675)

In [20]:
outgoing_edges_q1['in edges'].mean(), outgoing_edges_q2['in edges'].mean(), outgoing_edges_q3['in edges'].mean(), outgoing_edges_q4['in edges'].mean()

(3.9767507629944734, 3.667994296689959, 2.489977964483933, 11.101838813638212)

In [21]:
outgoing_edges_q1['out edges'].mean(), outgoing_edges_q2['out edges'].mean(), outgoing_edges_q3['out edges'].mean(), outgoing_edges_q4['out edges'].mean()

(0.0, 0.8123446024769334, 2.209997289749361, 18.214094232570744)

In [22]:
incoming_edges_bottom_1['in edges'].mean(), incoming_edges_top_1['in edges'].mean()

(0.0, 235.2441141848146)

In [23]:
incoming_edges_bottom_1['out edges'].mean(), incoming_edges_top_1['out edges'].mean()

(4.4613345117101195, 63.97998822836963)

In [24]:
outgoing_edges_bottom_1['in edges'].mean(), outgoing_edges_top_1['in edges'].mean()

(2.8858447488584473, 112.43952324896998)

In [25]:
outgoing_edges_bottom_1['out edges'].mean(), outgoing_edges_top_1['out edges'].mean()

(0.0, 160.2302825191289)

#### <i>Mean incoming and outgoing edges total network: $5.3$</i> 
#### <i>Sorted on number of incoming edges</i>
<table>
    <tr>
        <th>Group</th>
        <th>Mean #Incoming Edges</th>
        <th>Mean #Outgoing Edges</th>
    </tr>
    <tr>
        <td><i>Bottom 1%</i></td>
        <td>$0.00$</td>
        <td>$4.46$</td>
    </tr>
    <tr>
        <td>Q1 <i>(Bottom 25%)</i></td>
        <td>$0.00$</td>
        <td>$3.83$</td>
    </tr>
    <tr>
        <td>Q2</td>
        <td>$0.81$</td>
        <td>$2.36$</td>
    </tr>
    <tr>
        <td>Q3</td>
        <td>$1.82$</td>
        <td>$3.58$</td>
    </tr>
        <tr>
        <td>Q4 <i>(Top 25%)</i></td>
        <td>$18.6$</td>
        <td>$11.5$</td>
    </tr>
        <tr>
        <td><i>Top 1%</i></td>
        <td>$235$</td>
        <td>$64.0$</td>
    </tr>
</table>


#### <i>Sorted on number of outgoing edges</i>
<table>
    <tr>
        <th>Group</th>
        <th>Mean #Incoming Edges</th>
        <th>Mean #Outgoing Edges</th>
    </tr>
        <tr>
        <td><i>Bottom 1%</i></td>
        <td>$2.89$</td>
        <td>$0.00$</td>
    </tr>
    <tr>
        <td>Q1 <i>(Bottom 25%)</i></td>
        <td>$3.97$</td>
        <td>$0.00$</td>
    </tr>
    <tr>
        <td>Q2</td>
        <td>$3.67$</td>
        <td>$0.81$</td>
    </tr>
    <tr>
        <td>Q3</td>
        <td>$2.49$</td>
        <td>$2.21$</td>
    </tr>
        <tr>
        <td>Q4 <i>(Top 25%)</i></td>
        <td>$11.1$</td>
        <td>$18.2$</td>
    </tr>
        <tr>
        <td><i>Top 1%</i></td>
        <td>$112$</td>
        <td>$160$</td>
    </tr>
</table>


There are two noteworthy things in this graph. The nodes with a relatively high number of outgoing edges (i.e. the top $25\%$ or even the top $1\%$) also have a relatively high number of incoming edges when compared to the rest of the network. It thus seems that pages that have a lot of links to other pages also seem to be relatively high linked (i.e. have incoming edges) pages themselves  Note that there is a relatively large group (i.e. pages). The same can be seen in the top groups of when grouped/sorted by number of incoming edges. These groups do not only have a relatively higher number of incoming edges (on average) than the rest of the network, but also a relatively higher frequency of   in the network that do not have incoming edges, but have a relatively high number of outgoing edges.

In [26]:
print(str((wiki_df.loc[wiki_df["out edges"] == 0.00].shape[0] / wiki_df["out edges"].shape[0]) * 100), "%")
print(str((wiki_df.loc[wiki_df["in edges"] == 0.00].shape[0] / wiki_df["in edges"].shape[0]) * 100), "%")

29.691253735784134 %
29.83103724074137 %


In addition, one can see that part of the skewness of the degree distribution (see bottom groups) is due to pages that have either no incoming or outgoing edges. Having no incoming edges can be explained by pages that are the "entry-page" to this network of pages (i.e. referred to by somebody googling it / typing it in their address bar) while having no outgoing edges can be explained by pages that simply have no links on them (i.e. pages showing files etc.). These possible explanations are, however, just assumptions / guesses. There is no metadata about the pages available, so we can actually not confirm these hypotheses by more in-depth evaluations.

### <font color="darkgreen">2. Static Network Analysis:</font> Diameter

The next meausure which is going to be calculated and evaluated in the context of static network analysis is a grpah distance measure: the diameter. It encapsulates the maximum found eccentricity of any node in the network. Or in other words the longest of all the shortest paths between the vertices in the network. This may sound a bit confusing, but imagine that we have a set of all the shortest paths between each pair of vertices in the network. The maximum found value in this set is the diameter of the network. 

<b>A</b> --- <b>B</b> --- <b>C</b>&emsp;&emsp;&emsp; <i>Diameter:</i> $4$ (A-I and G-C) <br> 
|&emsp;&emsp;|&emsp;&emsp;| <br>
<b>D</b> --- <b>E</b> --- <b>F</b> <br>
|&emsp;&emsp;|&emsp;&emsp;| <br>
<b>G</b> --- <b>H</b> --- <b>I</b> 

<b>A</b> --- <b>B</b> --- <b>C</b>&emsp;&emsp;&emsp; <i>Diameter:</i> $5$  (A-J) <br> 
|&emsp;&emsp;|&emsp;&emsp;| <br>
<b>D</b> --- <b>E</b> --- <b>F</b> <br>
|&emsp;&emsp;|&emsp;&emsp;| <br>
<b>G</b> --- <b>H</b> --- <b>I</b> --- <b>J</b> 

This toyish example should give you a clear overview of what is measured by the distance measure that is diameter. Note, however, that this example is considering undirected edges, while we are of course interested in this measure of a directed graph of links. We will translate the measure back to our problem and network context in a bit.

Since we have a directed graph (i.e. network) that is not strongly connected since there are nodes $u$ which have no path to certain nodes $v$, we cannot simply use the diameter function of $networkx$ to calculate the diameter of the graph. The reason for this is a that if a shortest path from $u$ to $v$ is non-existent in the graph, it will be $\infty$ (think about Dijkstra's shortest path algorithm). And since the diameter function of $networkx$ simply calcultes the eccentricity of the Graph and returns the max value found in this collection, it will not work since the eccentricity function and thus the diameter function will raise an error because the graph is not strongly connected. 

A hack around this issue is pretty simple when one takes a look at the source code of $networkx$ (praise open-source software :)

In [27]:
nx.is_strongly_connected(G)

False

The problem with the built in $networkx$ function for calculating the diameter of a graphh is that the function relies on the eccentricity function. Eccentricity finds the shortest path from a node $u$ to all the other nodes and does this this for all the graphs in the network. The diameter function then calls this function on the graph and takes the max (i.e. longest shortest path) over the returned collection of all the shortest paths by eccentricity. 

But we still want to be able to calculate the diameter of this graph which is not strongly connected. Some code is devised below which transforms the original graph to a strongly connected graph by removing the nodes which make it 'weak', but after some evaluation we came to the conclusion that there is a risk of not finding the real diameter of the original graph. We, therefore, took a dive into the source code of $networkx$ and implement the function ourselves to fit our problem context and graph pecularities. The function is rather straigthforward, but unfortunately not very efficient. It is, however, exactly what is done under the hood in the functions of $networkx$ except the fact that we check whether there actually exists a path between a source node $u$ and a target node $v$ before actually calculating the shortest path between these nodes to prevent the function from returning 'infinity' and thus deteriorate the results.

In [28]:
'''
Make original graph strongly connected

nodes_in_strong_components = list(list(node)[0] for node in nx.strongly_connected_components(G))
gen_strong = G.nbunch_iter(nodes_in_strong_components)

edges_in_strong_components = nx.edges(G, nodes_in_strong_components)
self_loop_edges = list(nx.selfloop_edges(G))
edges_in_strong_components_no_loop = (set(edges_in_strong_components).difference(set(self_loop_edges)))
G_strong = G.edge_subgraph(edges_in_strong_components_no_loop)

entering_nodes = list(node for node in G_strong.nodes() if ((G_strong.in_degree(node) == 0) | (G_strong.out_degree(node) == 0)))
G_strong.remove_nodes_from(entering_nodes)
((len(G) - len(G_strong))/ len(G)) * 100
nx.is_strongly_connected(G_strong)

nx.diameter(G_strong, e = None, usebounds = False)

'''

'\nMake original graph strongly connected\n\nnodes_in_strong_components = list(list(node)[0] for node in nx.strongly_connected_components(G))\ngen_strong = G.nbunch_iter(nodes_in_strong_components)\n\nedges_in_strong_components = nx.edges(G, nodes_in_strong_components)\nself_loop_edges = list(nx.selfloop_edges(G))\nedges_in_strong_components_no_loop = (set(edges_in_strong_components).difference(set(self_loop_edges)))\nG_strong = G.edge_subgraph(edges_in_strong_components_no_loop)\n\nentering_nodes = list(node for node in G_strong.nodes() if ((G_strong.in_degree(node) == 0) | (G_strong.out_degree(node) == 0)))\nG_strong.remove_nodes_from(entering_nodes)\n((len(G) - len(G_strong))/ len(G)) * 100\nnx.is_strongly_connected(G_strong)\n\nnx.diameter(G_strong, e = None, usebounds = False)\n\n'

Since the function $nx.shortest\_path\_length$ relies on an implementation of Dijkstra's algorithm, the choice is made to remove the selfloop-edges since this (can) corrupt the results and the running time of the algorithm depending on the pecularities of the implementation of the algorithm.

In [29]:
self_loop_edges = list(nx.selfloop_edges(G))
edges_no_loop = list(set(G.edges()).difference(set(self_loop_edges)))
G_no_loop = G.edge_subgraph(edges_no_loop)
len(self_loop_edges) + len(edges_no_loop)== len(G.edges())

True

In [30]:
# edges_loops = nx.simple_cycles(G)

Calculating the longest shortest path in the network

In [31]:
def longest_shortest_path(G_in):
    max_distance = len(G_in) - 1
    longest = 0
    nodes = list(G_in.nodes())
    for u in nodes:
        for v in list(nx.dfs_successors(G_in, source = u)): # depth-first-search of successors
            if ((u != v) & (nx.has_path(G_in, u, v))):
                path_length = nx.shortest_path_length(G_in, source = u, target = v)
                if (path_length > longest):
                    longest = path_length
                    print("current longest: ", longest)
                    if(longest >= len(G_in)):
                        return max_distance
    return longest

The function could be optimized by implementing depth-first-search ourselves and comparing the shortest path-lengths along the way, but thay may be a bit far fetched for this analysis.

In [32]:
# diameter = longest_shortest_path(G_no_loop)

In [33]:
wiki_df.head()

node  in edges  out edges  decile_incoming_edges  decile_outgoing_edges
1    1        28         88                      0                      0
2    6        10          0                      0                      0
3    8        62          6                      0                      0
4    9      1375        477                      1                      1
5    3      1068        451                      1                      1

In [34]:
tracker = 0

In [35]:
def nr_successors_and_diameter_and_mean(node):
    node = str(node)
    total = mean = 0 # sum shortest path lengths
    longest = 0 # track longesth shortest path found
    
    successors = set(nx.dfs_successors(G, node))
    successors = list(successors - (set(node)))
    nr_paths = 0 # count paths for average
    
    for v in successors[-100:]:
        global tracker # track progress
        print("node: ", tracker)
        tracker += 1
        
        path_length = nx.shortest_path_length(G, source = node, target = v)
        nr_paths += 1
        total += path_length
        if (path_length > longest):
            longest = path_length
    if (nr_paths != 0):
        mean = int(total / nr_paths)
    return longest, mean, len(successors)

In [ ]:
wiki_df['longest_sp'], wiki_df['mean_sp'], wiki_df['nr_successors'] = zip(*wiki_df['node'].map(nr_successors_and_diameter_and_mean)) 

node:  0
node:  1
node:  2
node:  3
node:  4
node:  5
node:  6
node:  7
node:  8
node:  9
node:  10
node:  11
node:  12
node:  13
node:  14
node:  15
node:  16
node:  17
node:  18
node:  19
node:  20
node:  21
node:  22
node:  23
node:  24
node:  25
node:  26
node:  27
node:  28
node:  29
node:  30
node:  31
node:  32
node:  33
node:  34
node:  35
node:  36
node:  37
node:  38
node:  39
node:  40
node:  41
node:  42
node:  43
node:  44
node:  45
node:  46
node:  47
node:  48
node:  49
node:  50
node:  51
node:  52
node:  53
node:  54
node:  55
node:  56
node:  57
node:  58
node:  59
node:  60
node:  61
node:  62
node:  63
node:  64
node:  65
node:  66
node:  67
node:  68
node:  69
node:  70
node:  71
node:  72
node:  73
node:  74
node:  75
node:  76
node:  77
node:  78
node:  79
node:  80
node:  81
node:  82
node:  83
node:  84
node:  85
node:  86
node:  87
node:  88
node:  89
node:  90
node:  91
node:  92
node:  93
node:  94
node:  95
node:  96
node:  97
node:  98
node:  99
node:  100

node:  811
node:  812
node:  813
node:  814
node:  815
node:  816
node:  817
node:  818
node:  819
node:  820
node:  821
node:  822
node:  823
node:  824
node:  825
node:  826
node:  827
node:  828
node:  829
node:  830
node:  831
node:  832
node:  833
node:  834
node:  835
node:  836
node:  837
node:  838
node:  839
node:  840
node:  841
node:  842
node:  843
node:  844
node:  845
node:  846
node:  847
node:  848
node:  849
node:  850
node:  851
node:  852
node:  853
node:  854
node:  855
node:  856
node:  857
node:  858
node:  859
node:  860
node:  861
node:  862
node:  863
node:  864
node:  865
node:  866
node:  867
node:  868
node:  869
node:  870
node:  871
node:  872
node:  873
node:  874
node:  875
node:  876
node:  877
node:  878
node:  879
node:  880
node:  881
node:  882
node:  883
node:  884
node:  885
node:  886
node:  887
node:  888
node:  889
node:  890
node:  891
node:  892
node:  893
node:  894
node:  895
node:  896
node:  897
node:  898
node:  899
node:  900
node:  901

node:  1511
node:  1512
node:  1513
node:  1514
node:  1515
node:  1516
node:  1517
node:  1518
node:  1519
node:  1520
node:  1521
node:  1522
node:  1523
node:  1524
node:  1525
node:  1526
node:  1527
node:  1528
node:  1529
node:  1530
node:  1531
node:  1532
node:  1533
node:  1534
node:  1535
node:  1536
node:  1537
node:  1538
node:  1539
node:  1540
node:  1541
node:  1542
node:  1543
node:  1544
node:  1545
node:  1546
node:  1547
node:  1548
node:  1549
node:  1550
node:  1551
node:  1552
node:  1553
node:  1554
node:  1555
node:  1556
node:  1557
node:  1558
node:  1559
node:  1560
node:  1561
node:  1562
node:  1563
node:  1564
node:  1565
node:  1566
node:  1567
node:  1568
node:  1569
node:  1570
node:  1571
node:  1572
node:  1573
node:  1574
node:  1575
node:  1576
node:  1577
node:  1578
node:  1579
node:  1580
node:  1581
node:  1582
node:  1583
node:  1584
node:  1585
node:  1586
node:  1587
node:  1588
node:  1589
node:  1590
node:  1591
node:  1592
node:  1593
node

node:  2214
node:  2215
node:  2216
node:  2217
node:  2218
node:  2219
node:  2220
node:  2221
node:  2222
node:  2223
node:  2224
node:  2225
node:  2226
node:  2227
node:  2228
node:  2229
node:  2230
node:  2231
node:  2232
node:  2233
node:  2234
node:  2235
node:  2236
node:  2237
node:  2238
node:  2239
node:  2240
node:  2241
node:  2242
node:  2243
node:  2244
node:  2245
node:  2246
node:  2247
node:  2248
node:  2249
node:  2250
node:  2251
node:  2252
node:  2253
node:  2254
node:  2255
node:  2256
node:  2257
node:  2258
node:  2259
node:  2260
node:  2261
node:  2262
node:  2263
node:  2264
node:  2265
node:  2266
node:  2267
node:  2268
node:  2269
node:  2270
node:  2271
node:  2272
node:  2273
node:  2274
node:  2275
node:  2276
node:  2277
node:  2278
node:  2279
node:  2280
node:  2281
node:  2282
node:  2283
node:  2284
node:  2285
node:  2286
node:  2287
node:  2288
node:  2289
node:  2290
node:  2291
node:  2292
node:  2293
node:  2294
node:  2295
node:  2296
node

node:  2917
node:  2918
node:  2919
node:  2920
node:  2921
node:  2922
node:  2923
node:  2924
node:  2925
node:  2926
node:  2927
node:  2928
node:  2929
node:  2930
node:  2931
node:  2932
node:  2933
node:  2934
node:  2935
node:  2936
node:  2937
node:  2938
node:  2939
node:  2940
node:  2941
node:  2942
node:  2943
node:  2944
node:  2945
node:  2946
node:  2947
node:  2948
node:  2949
node:  2950
node:  2951
node:  2952
node:  2953
node:  2954
node:  2955
node:  2956
node:  2957
node:  2958
node:  2959
node:  2960
node:  2961
node:  2962
node:  2963
node:  2964
node:  2965
node:  2966
node:  2967
node:  2968
node:  2969
node:  2970
node:  2971
node:  2972
node:  2973
node:  2974
node:  2975
node:  2976
node:  2977
node:  2978
node:  2979
node:  2980
node:  2981
node:  2982
node:  2983
node:  2984
node:  2985
node:  2986
node:  2987
node:  2988
node:  2989
node:  2990
node:  2991
node:  2992
node:  2993
node:  2994
node:  2995
node:  2996
node:  2997
node:  2998
node:  2999
node

...

node:  339654
node:  339655
node:  339656
node:  339657
node:  339658
node:  339659
node:  339660
node:  339661
node:  339662
node:  339663
node:  339664
node:  339665
node:  339666
node:  339667
node:  339668
node:  339669
node:  339670
node:  339671
node:  339672
node:  339673
node:  339674
node:  339675
node:  339676
node:  339677
node:  339678
node:  339679
node:  339680
node:  339681
node:  339682
node:  339683
node:  339684
node:  339685
node:  339686
node:  339687
node:  339688
node:  339689
node:  339690
node:  339691
node:  339692
node:  339693
node:  339694
node:  339695
node:  339696
node:  339697
node:  339698
node:  339699
node:  339700
node:  339701
node:  339702
node:  339703
node:  339704
node:  339705
node:  339706
node:  339707
node:  339708
node:  339709
node:  339710
node:  339711
node:  339712
node:  339713
node:  339714
node:  339715
node:  339716
node:  339717
node:  339718
node:  339719
node:  339720
node:  339721
node:  339722
node:  339723
node:  339724
node: 

node:  340244
node:  340245
node:  340246
node:  340247
node:  340248
node:  340249
node:  340250
node:  340251
node:  340252
node:  340253
node:  340254
node:  340255
node:  340256
node:  340257
node:  340258
node:  340259
node:  340260
node:  340261
node:  340262
node:  340263
node:  340264
node:  340265
node:  340266
node:  340267
node:  340268
node:  340269
node:  340270
node:  340271
node:  340272
node:  340273
node:  340274
node:  340275
node:  340276
node:  340277
node:  340278
node:  340279
node:  340280
node:  340281
node:  340282
node:  340283
node:  340284
node:  340285
node:  340286
node:  340287
node:  340288
node:  340289
node:  340290
node:  340291
node:  340292
node:  340293
node:  340294
node:  340295
node:  340296
node:  340297
node:  340298
node:  340299
node:  340300
node:  340301
node:  340302
node:  340303
node:  340304
node:  340305
node:  340306
node:  340307
node:  340308
node:  340309
node:  340310
node:  340311
node:  340312
node:  340313
node:  340314
node: 

node:  341107
node:  341108
node:  341109
node:  341110
node:  341111
node:  341112
node:  341113
node:  341114
node:  341115
node:  341116
node:  341117
node:  341118
node:  341119
node:  341120
node:  341121
node:  341122
node:  341123
node:  341124
node:  341125
node:  341126
node:  341127
node:  341128
node:  341129
node:  341130
node:  341131
node:  341132
node:  341133
node:  341134
node:  341135
node:  341136
node:  341137
node:  341138
node:  341139
node:  341140
node:  341141
node:  341142
node:  341143
node:  341144
node:  341145
node:  341146
node:  341147
node:  341148
node:  341149
node:  341150
node:  341151
node:  341152
node:  341153
node:  341154
node:  341155
node:  341156
node:  341157
node:  341158
node:  341159
node:  341160
node:  341161
node:  341162
node:  341163
node:  341164
node:  341165
node:  341166
node:  341167
node:  341168
node:  341169
node:  341170
node:  341171
node:  341172
node:  341173
node:  341174
node:  341175
node:  341176
node:  341177
node: 

node:  341857
node:  341858
node:  341859
node:  341860
node:  341861
node:  341862
node:  341863
node:  341864
node:  341865
node:  341866
node:  341867
node:  341868
node:  341869
node:  341870
node:  341871
node:  341872
node:  341873
node:  341874
node:  341875
node:  341876
node:  341877
node:  341878
node:  341879
node:  341880
node:  341881
node:  341882
node:  341883
node:  341884
node:  341885
node:  341886
node:  341887
node:  341888
node:  341889
node:  341890
node:  341891
node:  341892
node:  341893
node:  341894
node:  341895
node:  341896
node:  341897
node:  341898
node:  341899
node:  341900
node:  341901
node:  341902
node:  341903
node:  341904
node:  341905
node:  341906
node:  341907
node:  341908
node:  341909
node:  341910
node:  341911
node:  341912
node:  341913
node:  341914
node:  341915
node:  341916
node:  341917
node:  341918
node:  341919
node:  341920
node:  341921
node:  341922
node:  341923
node:  341924
node:  341925
node:  341926
node:  341927
node: 

node:  342444
node:  342445
node:  342446
node:  342447
node:  342448
node:  342449
node:  342450
node:  342451
node:  342452
node:  342453
node:  342454
node:  342455
node:  342456
node:  342457
node:  342458
node:  342459
node:  342460
node:  342461
node:  342462
node:  342463
node:  342464
node:  342465
node:  342466
node:  342467
node:  342468
node:  342469
node:  342470
node:  342471
node:  342472
node:  342473
node:  342474
node:  342475
node:  342476
node:  342477
node:  342478
node:  342479
node:  342480
node:  342481
node:  342482
node:  342483
node:  342484
node:  342485
node:  342486
node:  342487
node:  342488
node:  342489
node:  342490
node:  342491
node:  342492
node:  342493
node:  342494
node:  342495
node:  342496
node:  342497
node:  342498
node:  342499
node:  342500
node:  342501
node:  342502
node:  342503
node:  342504
node:  342505
node:  342506
node:  342507
node:  342508
node:  342509
node:  342510
node:  342511
node:  342512
node:  342513
node:  342514
node: 

### <font color="red">To-do: Implication of the value of the distance measure in relation to our problem contex/the characteristics of the network.</font>

### <font color="darkgreen">3. Static Network Analysis:</font> Mean shortest-path length

The next statistical measure in this static network analysis has a strong relationship to the previous statistical measure. While the diameter captured the maximum eccentricity (i.e. the greatest distance between any pair of nodes in the network) found among all the nodes in the graph, the mean shortest-path length is a metric that captures the average distance (i.e. shortest path) between any pair of vertices in the graph.

There are a few things to consider before we can actually continue with the evaluation of this metric. As we know by know the graph view (ignoring the time-stamps) that is taken in this static network analysis contains selfloop-edges and many other peculartities that can deterioriate the calculation of the means-shortest-path length and thus affect any implications that are going to be suggested after the evaluation of the result in our the context of our network.

The choice is made to calculate the mean shortest-path length across all the pairs of vertices $u$ and $v$ in the graph where 1) $u\, !=\, v$ and  2) there exist a path from $u$ to $v$ (would otherwise result in $\infty$)

### <font color="darkgreen">4. Static Network Analysis:</font> Betweenness centrality

In [ ]:
# nx.betweenness_centrality(G)

### <font color="darkgreen">5. Static Network Analysis:</font> Closeness centrality